In [ ]:
import autogen

config_list = autogen.config_list_from_json(env_or_file="OAI_CONFIG_LIST")

llm_config={
    "request_timeout": 600,
    "seed": 42,
    "config_list": config_list,
    "temperature": 0,
}

In [ ]:
assistant = autogen.AssistantAgent(
    name="assistant",
    llm_config=llm_config,
    is_termination_msg=lambda x: True if "TERMINATE" in x.get("content") else False,
)

user_proxy = autogen.UserProxyAgent(
    name="user_proxy",
    human_input_mode="NEVER",
    is_termination_msg=lambda x: True if "TERMINATE" in x.get("content") else False,
    max_consecutive_auto_reply=10,
    code_execution_config={
        "work_dir": "work_dir",
        "use_docker": True,
    },
)

In [ ]:
task1 = """
Give me the cheapest Vueling daily flight between Barcelona and Palma for everyday of next month.
The URL to obtain it is this one:
https://apiwww.vueling.com/api/FlightPrice/GetAllFlights?originCode={departure_station}&destinationCode={arrival_station}&year={year}&month={month}&currencyCode={currency_code}&monthsRange=17
The 'departure_station' and 'arrival_station' parameters must be in IATA Code. Example: BCN, MAD, LCG." 
If the 'departure_station' or the 'arrival_station' is not in IATA code you must do the convertion. Example: Madrid = MAD
The 'month' needs to be a number. If the 'month' given to you is not a number, then you must convert it. Example: February = 2

The output of the calling call looks like this:
[
    {
        "ArrivalDate": "2023-11-01T00:00:00",
        "ArrivalStation": "CDG",
        "Availability": 0,
        "ClassOfService": "C",
        "Created": "0001-01-01T00:00:00",
        "DepartureDate": "2023-11-01T06:00:00",
        "DepartureStation": "BCN",
        "Fare": null,
        "FlightID": "8242",
        "Price": 119.99,
        "ProductClass": null,
        "Sort": 0,
        "Tax": 0.0,
        "IsInvalidPrice": false
    }
]

Return the data in this format:
vueling_prices = [
    "2023-11-01": 17.46,
    "2023-11-02": 19.46,
    ...
]    
"""

user_proxy.initiate_chat(assistant, message=task1)

In [ ]:
task2 = """
Give me the cheapest Ryanair daily flight between Barcelona and Palma for everyday of next month.
The URL to obtain it is this one:
https://services-api.ryanair.com/farfnd/3/oneWayFares/{departure_station}/{arrival_station}/cheapestPerDay?outboundMonthOfDate={year}-{month}-01
The 'departure_station' and 'arrival_station' parameters must be in IATA Code. Example: BCN, MAD, LCG." 
If the 'departure_station' or the 'arrival_station' is not in IATA code you must do the convertion. Example: Madrid = MAD
The 'month' and 'year' needs to be a number. If the 'month' or 'year' given to you is not a number, then you must convert it. Example: February = 2
You don't need to make multiple calls for every day of the month. A single request to the first day of the month will give you the cheapest prices for the entire month.

Return the data in this format:
ryanair_prices = [
    "2023-11-01": 17.46,
    "2023-11-02": 19.46,
    ...
]  
"""

user_proxy.initiate_chat(assistant, message=task2, clear_history=False)

In [ ]:
task3 = """Use this data to generate a chart comparing the cheapest daily prices between Vueling and Ryanair flights.
Save the chart in a png file
"""
user_proxy.initiate_chat(assistant, message=task3, clear_history=False)